<a href="https://colab.research.google.com/github/jiku100/ShadowDetectionMethod/blob/main/DeepLearning/BDRAR_EX/BDRAR_EX.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
from google.colab import drive
drive.mount('/content/gdrive')

Mounted at /content/gdrive


In [ ]:
!cp -r "/content/gdrive/My Drive/BDRAR_EX" .

In [ ]:
%cd BDRAR_EX

/content/BDRAR_EX


In [ ]:
import sys
sys.path.append('/content/BDRAR_EX/model')
print(sys.path)

['', '/content', '/env/python', '/usr/lib/python37.zip', '/usr/lib/python3.7', '/usr/lib/python3.7/lib-dynload', '/usr/local/lib/python3.7/dist-packages', '/usr/lib/python3/dist-packages', '/usr/local/lib/python3.7/dist-packages/IPython/extensions', '/root/.ipython', '/content/BDRAR_EX/model']


In [ ]:
!pip install git+https://github.com/lucasb-eyer/pydensecrf.git

  Cloning https://github.com/lucasb-eyer/pydensecrf.git to /tmp/pip-req-build-d_crzdjh
  Running command git clone -q https://github.com/lucasb-eyer/pydensecrf.git /tmp/pip-req-build-d_crzdjh
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
    Preparing wheel metadata ... done
  Created wheel for pydensecrf: filename=pydensecrf-1.0rc2-cp37-cp37m-linux_x86_64.whl size=2774292 sha256=36bb34373b348cdc8791973266922ec1624ae16124c7604fd00785e08e15415e
  Stored in directory: /tmp/pip-ephem-wheel-cache-917io5p2/wheels/81/ac/ed/09f1890b954ca1ff7f189518cc9a319138e50e7ea88937fae9
Successfully built pydensecrf


# 1. Only BDRAR_EX

In [ ]:
!unzip SBU_Train.zip

In [ ]:
import datetime
import os
import datetime

import torch
from torch import nn
from torch import optim
from torch.autograd import Variable
from torch.backends import cudnn
from torch.utils.data import DataLoader
from torchvision import transforms


from model.BDRAR_EX import BDRAR_EX
from dataloaders.SBU import SBU
from dataloaders import joint_transforms
from utils.util import AvgMeter, check_mkdir

cudnn.benchmark = True

torch.cuda.set_device(0)

root = './'
ckpt_path = './ckpt'
exp_name = 'BDRAR_EX'

# batch size of 8 with resolution of 416*416 is exactly OK for the GTX 1080Ti GPU
args = {
    'iter_num': 5000,
    'train_batch_size': 8,
    'last_iter': 0,
    'lr': 5e-3,
    'lr_decay': 0.9,
    'weight_decay': 5e-4,
    'momentum': 0.9,
    'snapshot': '',
    'scale': 416
}

joint_transform = joint_transforms.Compose([
        joint_transforms.RandomHorizontallyFlip(),
        joint_transforms.Resize((416, 416))
    ])
src1_transform = transforms.Compose([
        transforms.ToTensor(),
        transforms.Normalize([0.485, 0.456, 0.406], [0.229, 0.224, 0.225])
    ])
src2_transform = transforms.Compose([
        transforms.ToTensor(),
        transforms.Normalize([0.5, 0.5, 0.5], [0.5, 0.5, 0.5])
    ])
target_transform = transforms.ToTensor()
to_pil = transforms.ToPILImage()

db_train = SBU(root=root, joint_transform = joint_transform, src1_transform = src1_transform, src2_transform = src2_transform, target_transform = target_transform)
train_loader = DataLoader(db_train, batch_size=4, num_workers=8, shuffle=True)

bce_logit = nn.BCEWithLogitsLoss().cuda()
log_path = os.path.join(ckpt_path, exp_name, str(datetime.datetime.now()) + '.txt')


def main():
    net = BDRAR_EX().cuda().train()

    optimizer = optim.SGD([
        {'params': [param for name, param in net.named_parameters() if name[-4:] == 'bias'],
         'lr': 2 * args['lr']},
        {'params': [param for name, param in net.named_parameters() if name[-4:] != 'bias'],
         'lr': args['lr'], 'weight_decay': args['weight_decay']}
    ], momentum=args['momentum'])

    if len(args['snapshot']) > 0:
        print('training resumes from \'%s\'' % args['snapshot'])
        net.load_state_dict(torch.load(os.path.join(ckpt_path, exp_name, args['snapshot'] + '.pth')))
        optimizer.load_state_dict(torch.load(os.path.join(ckpt_path, exp_name, args['snapshot'] + '_optim.pth')))
        optimizer.param_groups[0]['lr'] = 2 * args['lr']
        optimizer.param_groups[1]['lr'] = args['lr']

    check_mkdir(ckpt_path)
    check_mkdir(os.path.join(ckpt_path, exp_name))
    open(log_path, 'w').write(str(args) + '\n\n')
    train(net, optimizer)


def train(net, optimizer):
    curr_iter = args['last_iter']
    while True:
        train_loss_record, loss_fuse_record, loss1_h2l_record = AvgMeter(), AvgMeter(), AvgMeter()
        loss2_h2l_record, loss3_h2l_record, loss4_h2l_record = AvgMeter(), AvgMeter(), AvgMeter()
        loss1_l2h_record, loss2_l2h_record, loss3_l2h_record = AvgMeter(), AvgMeter(), AvgMeter()
        loss4_l2h_record = AvgMeter()

        for i, data in enumerate(train_loader):
            optimizer.param_groups[0]['lr'] = 2 * args['lr'] * (1 - float(curr_iter) / args['iter_num']
                                                                ) ** args['lr_decay']
            optimizer.param_groups[1]['lr'] = args['lr'] * (1 - float(curr_iter) / args['iter_num']
                                                            ) ** args['lr_decay']

            with torch.autograd.set_detect_anomaly(True):
                src1, src2, target = data['src1'], data['src2'], data['target']
                batch_size = src1.size(0)
                src1 = Variable(src1).cuda()
                src2 = Variable(src2).cuda()
                target = Variable(target).cuda()

            

                optimizer.zero_grad()

                fuse_predict, predict1_h2l, predict2_h2l, predict3_h2l, predict4_h2l, \
                predict1_l2h, predict2_l2h, predict3_l2h, predict4_l2h = net.forward(src1, src2)
                loss_fuse = bce_logit(fuse_predict, target)
                loss1_h2l = bce_logit(predict1_h2l, target)
                loss2_h2l = bce_logit(predict2_h2l, target)
                loss3_h2l = bce_logit(predict3_h2l, target)
                loss4_h2l = bce_logit(predict4_h2l, target)
                loss1_l2h = bce_logit(predict1_l2h, target)
                loss2_l2h = bce_logit(predict2_l2h, target)
                loss3_l2h = bce_logit(predict3_l2h, target)
                loss4_l2h = bce_logit(predict4_l2h, target)

                loss = loss_fuse + loss1_h2l + loss2_h2l + loss3_h2l + loss4_h2l + loss1_l2h + loss2_l2h + loss3_l2h + loss4_l2h
                loss.backward()
                optimizer.step()

                train_loss_record.update(loss.data, batch_size)
                loss_fuse_record.update(loss_fuse.data, batch_size)
                loss1_h2l_record.update(loss1_h2l.data, batch_size)
                loss2_h2l_record.update(loss2_h2l.data, batch_size)
                loss3_h2l_record.update(loss3_h2l.data, batch_size)
                loss4_h2l_record.update(loss4_h2l.data, batch_size)
                loss1_l2h_record.update(loss1_l2h.data, batch_size)
                loss2_l2h_record.update(loss2_l2h.data, batch_size)
                loss3_l2h_record.update(loss3_l2h.data, batch_size)
                loss4_l2h_record.update(loss4_l2h.data, batch_size)

            curr_iter += 1

            log = '[iter %d], [train loss %.5f], [loss_fuse %.5f], [loss1_h2l %.5f], [loss2_h2l %.5f], ' \
                  '[loss3_h2l %.5f], [loss4_h2l %.5f], [loss1_l2h %.5f], [loss2_l2h %.5f], [loss3_l2h %.5f], ' \
                  '[loss4_l2h %.5f], [lr %.13f]' % \
                  (curr_iter, train_loss_record.avg, loss_fuse_record.avg, loss1_h2l_record.avg, loss2_h2l_record.avg,
                   loss3_h2l_record.avg, loss4_h2l_record.avg, loss1_l2h_record.avg, loss2_l2h_record.avg,
                   loss3_l2h_record.avg, loss4_l2h_record.avg, optimizer.param_groups[1]['lr'])
            print(log)
            open(log_path, 'a').write(log + '\n')

            if curr_iter >= args['iter_num']:
                date = datetime.datetime.now().strftime('%Y-%m-%d %H:%M:%S')
                torch.save(net.state_dict(), os.path.join("gradient_5000.pth"))
                return


if __name__ == '__main__':
    main()

/usr/local/lib/python3.7/dist-packages/torch/utils/data/dataloader.py:477: UserWarning: This DataLoader will create 8 worker processes in total. Our suggested max number of worker in current system is 2, which is smaller than what this DataLoader is going to create. Please be aware that excessive worker creation might get DataLoader running slow or even freeze, lower the worker number to avoid potential slowness/freeze if necessary.
  cpuset_checked))
/usr/local/lib/python3.7/dist-packages/torch/nn/functional.py:3458: UserWarning: Default upsampling behavior when mode=bilinear is changed to align_corners=False since 0.4.0. Please specify align_corners=True if the old behavior is desired. See the documentation of nn.Upsample for details.
  "See the documentation of nn.Upsample for details.".format(mode)


[iter 1], [train loss 6.44346], [loss_fuse 0.71437], [loss1_h2l 0.71250], [loss2_h2l 0.71484], [loss3_h2l 0.71434], [loss4_h2l 0.72443], [loss1_l2h 0.72296], [loss2_l2h 0.71452], [loss3_l2h 0.71215], [loss4_l2h 0.71336], [lr 0.0050000000000]
[iter 2], [train loss 6.43106], [loss_fuse 0.71404], [loss1_h2l 0.71545], [loss2_h2l 0.71707], [loss3_h2l 0.71461], [loss4_h2l 0.71946], [loss1_l2h 0.71688], [loss2_l2h 0.71259], [loss3_l2h 0.71023], [loss4_l2h 0.71072], [lr 0.0049990999910]
[iter 3], [train loss 6.31593], [loss_fuse 0.70074], [loss1_h2l 0.70411], [loss2_h2l 0.70374], [loss3_h2l 0.70060], [loss4_h2l 0.70454], [loss1_l2h 0.70418], [loss2_l2h 0.70069], [loss3_l2h 0.69841], [loss4_l2h 0.69894], [lr 0.0049981999640]
[iter 4], [train loss 6.23513], [loss_fuse 0.69108], [loss1_h2l 0.69526], [loss2_h2l 0.69588], [loss3_h2l 0.69287], [loss4_h2l 0.69443], [loss1_l2h 0.69384], [loss2_l2h 0.69134], [loss3_l2h 0.68978], [loss4_l2h 0.69065], [lr 0.0049972999190]
[iter 5], [train loss 6.17478], 

# 2. BDRAR_EX + MTMT

In [ ]:
!cp -r "/content/gdrive/MyDrive/MTMT/UnionTrain.zip" .
!unzip UnionTrain.zip

In [ ]:
import datetime
import os
import datetime
import random 
from tqdm import tqdm

import torch
from torch import nn
from torch import optim
from torch.autograd import Variable
from torch.backends import cudnn
from torch.utils.data import DataLoader
from torchvision import transforms
import torch.nn.functional as F

from model.BDRAR_EX import BDRAR_EX
from utils import ramps
from dataloaders import joint_transforms
from utils.util import AvgMeter, check_mkdir, TwoStreamBatchSampler
from dataloaders.SBU import SBU_MTMT, relabel_dataset
from dataloaders import joint_transforms

cudnn.benchmark = True

torch.cuda.set_device(0)

root = './UnionTrain'
ckpt_path = './ckpt'
exp_name = 'BDRAR_EX'

# batch size of 8 with resolution of 416*416 is exactly OK for the GTX 1080Ti GPU
args = {
    'iter_num': 5000,
    'train_batch_size': 8,
    'last_iter': 0,
    'lr': 5e-3,
    'lr_decay': 0.9,
    'ema_decay' : 0.99,
    'weight_decay': 5e-4,
    'momentum': 0.9,
    'snapshot': '',
    'scale': 416,
    'seed': 1337,
    'consistency' : 1,
    'consistency_rampup' : 7.0
}

cudnn.benchmark = True

torch.cuda.set_device(0)

joint_transform = joint_transforms.Compose([
        joint_transforms.RandomHorizontallyFlip(),
        joint_transforms.Resize((416, 416))
    ])
src1_transform = transforms.Compose([
        transforms.ToTensor(),
        transforms.Normalize([0.485, 0.456, 0.406], [0.229, 0.224, 0.225])
    ])
src2_transform = transforms.Compose([
        transforms.ToTensor(),
        transforms.Normalize([0.5, 0.5, 0.5], [0.5, 0.5, 0.5])
    ])
target_transform = transforms.ToTensor()
to_pil = transforms.ToPILImage()

bce_logit = nn.BCEWithLogitsLoss().cuda()
log_path = os.path.join(ckpt_path, exp_name, str(datetime.datetime.now()) + '.txt')



def get_current_consistency_weight(epoch):
    # Consistency ramp-up from https://arxiv.org/abs/1610.02242
    return args['consistency'] * ramps.sigmoid_rampup(epoch, args['consistency_rampup'])

def update_ema_variables(model, ema_model, alpha, global_step):
    # Use the true average until the exponential average is more correct
    alpha = min(1 - 1 / (global_step + 1), alpha)
    for ema_param, param in zip(ema_model.parameters(), model.parameters()):
        ema_param.data.mul_(alpha).add_(1 - alpha, param.data)
    
def sigmoid_mse_loss(input_logits, target_logits):
    input_sigmoid = F.sigmoid(input_logits)
    target_sigmoid = F.sigmoid(target_logits)
    return F.mse_loss(input_sigmoid, target_sigmoid, reduction='mean')

batch_size = 3
labeled_bs = 2
consistency_criterion = sigmoid_mse_loss

db_train = SBU_MTMT(root=root, joint_transform = joint_transform, src1_transform = src1_transform, src2_transform = src2_transform, target_transform = target_transform)
labeled_idxs, unlabeled_idxs = relabel_dataset(db_train)
batch_sampler = TwoStreamBatchSampler(labeled_idxs, unlabeled_idxs, batch_size, batch_size-labeled_bs)

def worker_init_fn(worker_id):
    random.seed(args['seed']+worker_id)

trainloader = DataLoader(db_train, batch_sampler=batch_sampler, num_workers=4, worker_init_fn = worker_init_fn)
max_epoch = args['iter_num']//len(trainloader)+1

def main():
    student = BDRAR_EX().cuda().train()
    teacher = BDRAR_EX().cuda().train()

    optimizer = optim.SGD([
        {'params': [param for name, param in student.named_parameters() if name[-4:] == 'bias'],
         'lr': 2 * args['lr']},
        {'params': [param for name, param in student.named_parameters() if name[-4:] != 'bias'],
         'lr': args['lr'], 'weight_decay': args['weight_decay']}
    ], momentum=args['momentum'])

    if len(args['snapshot']) > 0:
        print('training resumes from \'%s\'' % args['snapshot'])
        net.load_state_dict(torch.load(os.path.join(ckpt_path, exp_name, args['snapshot'] + '.pth')))
        optimizer.load_state_dict(torch.load(os.path.join(ckpt_path, exp_name, args['snapshot'] + '_optim.pth')))
        optimizer.param_groups[0]['lr'] = 2 * args['lr']
        optimizer.param_groups[1]['lr'] = args['lr']

    check_mkdir(ckpt_path)
    check_mkdir(os.path.join(ckpt_path, exp_name))
    open(log_path, 'w').write(str(args) + '\n\n')
    train(student, teacher, optimizer)

def train(student, teacher, optimizer):
    curr_iter = args['last_iter']
    for epoch_num in tqdm(range(max_epoch), ncols=70):
        train_loss_record, supervised_loss_record, consistency_loss_record = AvgMeter(), AvgMeter(), AvgMeter()

        for i, data in enumerate(trainloader):
            optimizer.param_groups[0]['lr'] = 2 * args['lr'] * (1 - float(curr_iter) / args['iter_num']
                                                                ) ** args['lr_decay']
            optimizer.param_groups[1]['lr'] = args['lr'] * (1 - float(curr_iter) / args['iter_num']
                                                            ) ** args['lr_decay']

            with torch.autograd.set_detect_anomaly(True):
                src1, src2, target = data['src1'], data['src2'], data['target']
                batch_size = src1.size(0)
                src1, src2, target = src1.cuda(), src2.cuda(), target.cuda()

                noise = torch.clamp(torch.randn_like(src1) * 0.1, -0.2, 0.2)
                ema_src1 = src1 + noise
                ema_src2 = src2 + noise            

                optimizer.zero_grad()

                fuse_predict, predict1_h2l, predict2_h2l, predict3_h2l, predict4_h2l, \
                predict1_l2h, predict2_l2h, predict3_l2h, predict4_l2h = student.forward(src1, src2)

                with torch.no_grad():
                  fuse_predict_ema, predict1_h2l_ema, predict2_h2l_ema, predict3_h2l_ema, predict4_h2l_ema, \
                  predict1_l2h_ema, predict2_l2h_ema, predict3_l2h_ema, predict4_l2h_ema = teacher.forward(ema_src1, ema_src2)

                loss_fuse = bce_logit(fuse_predict[:labeled_bs], target[:labeled_bs])
                loss1_h2l = bce_logit(predict1_h2l[:labeled_bs], target[:labeled_bs])
                loss2_h2l = bce_logit(predict2_h2l[:labeled_bs], target[:labeled_bs])
                loss3_h2l = bce_logit(predict3_h2l[:labeled_bs], target[:labeled_bs])
                loss4_h2l = bce_logit(predict4_h2l[:labeled_bs], target[:labeled_bs])
                loss1_l2h = bce_logit(predict1_l2h[:labeled_bs], target[:labeled_bs])
                loss2_l2h = bce_logit(predict2_l2h[:labeled_bs], target[:labeled_bs])
                loss3_l2h = bce_logit(predict3_l2h[:labeled_bs], target[:labeled_bs])
                loss4_l2h = bce_logit(predict4_l2h[:labeled_bs], target[:labeled_bs])

                supervised_loss = loss_fuse + loss1_h2l + loss2_h2l + loss3_h2l + loss4_h2l + loss1_l2h + loss2_l2h + loss3_l2h + loss4_l2h

                loss_fuse_con = consistency_criterion(fuse_predict[labeled_bs:], fuse_predict_ema[labeled_bs:])
                loss1_h2l_con = consistency_criterion(predict1_h2l[labeled_bs:], predict1_h2l_ema[labeled_bs:])
                loss2_h2l_con = consistency_criterion(predict2_h2l[labeled_bs:], predict2_h2l_ema[labeled_bs:])
                loss3_h2l_con = consistency_criterion(predict3_h2l[labeled_bs:], predict3_h2l_ema[labeled_bs:])
                loss4_h2l_con = consistency_criterion(predict4_h2l[labeled_bs:], predict4_h2l_ema[labeled_bs:])
                loss1_l2h_con = consistency_criterion(predict1_l2h[labeled_bs:], predict1_l2h_ema[labeled_bs:])
                loss2_l2h_con = consistency_criterion(predict2_l2h[labeled_bs:], predict2_l2h_ema[labeled_bs:])
                loss3_l2h_con = consistency_criterion(predict3_l2h[labeled_bs:], predict3_l2h_ema[labeled_bs:])
                loss4_l2h_con = consistency_criterion(predict4_l2h[labeled_bs:], predict4_l2h_ema[labeled_bs:])
                
                consistency_weight = get_current_consistency_weight(epoch_num)
                consistency_loss = consistency_weight*(loss_fuse_con + loss1_h2l_con + loss2_h2l_con + loss3_h2l_con + loss4_h2l_con + loss1_l2h_con + loss2_l2h_con + loss3_l2h_con + loss4_l2h_con)

                loss = supervised_loss + consistency_loss

                loss.backward()
                optimizer.step()
                update_ema_variables(student, teacher, args['ema_decay'], curr_iter)


                train_loss_record.update(loss.data, batch_size)
                supervised_loss_record.update(supervised_loss.data, batch_size)
                consistency_loss_record.update(consistency_loss.data, batch_size)
                

            curr_iter += 1

            log = '[iter %d], [train loss %.5f], [supervised_loss %.5f], [consistency_loss %.5f], [lr %.13f]' % \
                  (curr_iter, train_loss_record.avg, supervised_loss_record.avg, consistency_loss_record.avg, optimizer.param_groups[1]['lr'])
            print(log)
            open(log_path, 'a').write(log + '\n')

            if curr_iter >= args['iter_num']:
                torch.save(student.state_dict(), os.path.join("gradient_MTMT3.pth"))
                return
    if curr_iter >= args['iter_num']:
                torch.save(student.state_dict(), os.path.join("gradient_MTMT3.pth"))
                return


if __name__ == '__main__':
    main()

  0%|                                           | 0/3 [00:00<?, ?it/s]/usr/local/lib/python3.7/dist-packages/torch/nn/functional.py:3458: UserWarning: Default upsampling behavior when mode=bilinear is changed to align_corners=False since 0.4.0. Please specify align_corners=True if the old behavior is desired. See the documentation of nn.Upsample for details.
  "See the documentation of nn.Upsample for details.".format(mode)
/usr/local/lib/python3.7/dist-packages/torch/nn/functional.py:1709: UserWarning: nn.functional.sigmoid is deprecated. Use torch.sigmoid instead.
  warnings.warn("nn.functional.sigmoid is deprecated. Use torch.sigmoid instead.")
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:80: UserWarning: This overload of add_ is deprecated:
	add_(Number alpha, Tensor other)
Consider using one of the following signatures instead:
	add_(Tensor other, *, Number alpha) (Triggered internally at  /pytorch/torch/csrc/utils/python_arg_parser.cpp:1005.)


[iter 1], [train loss 6.46160], [supervised_loss 6.45978], [consistency_loss 0.00181], [lr 0.0050000000000]
[iter 2], [train loss 6.55060], [supervised_loss 6.54968], [consistency_loss 0.00092], [lr 0.0049990999910]
[iter 3], [train loss 6.45121], [supervised_loss 6.45059], [consistency_loss 0.00062], [lr 0.0049981999640]
[iter 4], [train loss 6.29754], [supervised_loss 6.29705], [consistency_loss 0.00050], [lr 0.0049972999190]
[iter 5], [train loss 6.04387], [supervised_loss 6.04342], [consistency_loss 0.00044], [lr 0.0049963998560]
[iter 6], [train loss 5.79383], [supervised_loss 5.79338], [consistency_loss 0.00045], [lr 0.0049954997749]
[iter 7], [train loss 5.67470], [supervised_loss 5.67420], [consistency_loss 0.00050], [lr 0.0049945996759]
[iter 8], [train loss 5.49142], [supervised_loss 5.49084], [consistency_loss 0.00058], [lr 0.0049936995588]
[iter 9], [train loss 5.30319], [supervised_loss 5.30253], [consistency_loss 0.00066], [lr 0.0049927994237]
[iter 10], [train loss 5.280

 33%|█████████▋                   | 1/3 [1:06:44<2:13:28, 4004.48s/it]

[iter 2042], [train loss 2.27117], [supervised_loss 2.27092], [consistency_loss 0.00025], [lr 0.0031183687461]
[iter 2043], [train loss 1.89497], [supervised_loss 1.89323], [consistency_loss 0.00174], [lr 0.0031174202570]
[iter 2044], [train loss 1.70482], [supervised_loss 1.70317], [consistency_loss 0.00165], [lr 0.0031164717358]
[iter 2045], [train loss 1.74468], [supervised_loss 1.74160], [consistency_loss 0.00308], [lr 0.0031155231826]
[iter 2046], [train loss 1.68980], [supervised_loss 1.68695], [consistency_loss 0.00284], [lr 0.0031145745972]
[iter 2047], [train loss 1.49879], [supervised_loss 1.49604], [consistency_loss 0.00275], [lr 0.0031136259798]
[iter 2048], [train loss 1.38137], [supervised_loss 1.37886], [consistency_loss 0.00251], [lr 0.0031126773302]
[iter 2049], [train loss 1.43749], [supervised_loss 1.43524], [consistency_loss 0.00226], [lr 0.0031117286485]
[iter 2050], [train loss 2.10975], [supervised_loss 2.10769], [consistency_loss 0.00206], [lr 0.0031107799347]
[

 67%|███████████████████▎         | 2/3 [2:12:50<1:06:32, 3992.94s/it]

[iter 4084], [train loss 1.96984], [supervised_loss 1.96927], [consistency_loss 0.00058], [lr 0.0010864991791]
[iter 4085], [train loss 2.25618], [supervised_loss 2.25432], [consistency_loss 0.00185], [lr 0.0010854327641]
[iter 4086], [train loss 3.76682], [supervised_loss 3.76548], [consistency_loss 0.00134], [lr 0.0010843662326]
[iter 4087], [train loss 2.94588], [supervised_loss 2.94479], [consistency_loss 0.00109], [lr 0.0010832995846]
[iter 4088], [train loss 2.83802], [supervised_loss 2.83686], [consistency_loss 0.00115], [lr 0.0010822328198]
[iter 4089], [train loss 2.64784], [supervised_loss 2.64622], [consistency_loss 0.00162], [lr 0.0010811659382]
[iter 4090], [train loss 2.41860], [supervised_loss 2.41708], [consistency_loss 0.00153], [lr 0.0010800989396]
[iter 4091], [train loss 2.21916], [supervised_loss 2.21769], [consistency_loss 0.00146], [lr 0.0010790318239]
[iter 4092], [train loss 2.08624], [supervised_loss 2.08476], [consistency_loss 0.00148], [lr 0.0010779645909]
[

# 3. BDRAR

In [ ]:
!unzip SBU_Train.zip

스트리밍 출력 내용이 길어서 마지막 5000줄이 삭제되었습니다.
  inflating: ShadowImages/lssd3853.jpg  
  inflating: ShadowImages/lssd3854.jpg  
  inflating: ShadowImages/lssd3855.jpg  
  inflating: ShadowImages/lssd3856.jpg  
  inflating: ShadowImages/lssd3857.jpg  
  inflating: ShadowImages/lssd3858.jpg  
  inflating: ShadowImages/lssd3859.jpg  
  inflating: ShadowImages/lssd386.jpg  
  inflating: ShadowImages/lssd3860.jpg  
  inflating: ShadowImages/lssd3861.jpg  
  inflating: ShadowImages/lssd3862.jpg  
  inflating: ShadowImages/lssd3863.jpg  
  inflating: ShadowImages/lssd3864.jpg  
  inflating: ShadowImages/lssd3865.jpg  
  inflating: ShadowImages/lssd3866.jpg  
  inflating: ShadowImages/lssd3867.jpg  
  inflating: ShadowImages/lssd3868.jpg  
  inflating: ShadowImages/lssd3869.jpg  
  inflating: ShadowImages/lssd387.jpg  
  inflating: ShadowImages/lssd3870.jpg  
  inflating: ShadowImages/lssd3871.jpg  
  inflating: ShadowImages/lssd3872.jpg  
  inflating: ShadowImages/lssd3873.jpg  
  inflating: ShadowImag

In [ ]:
import datetime
import os
import datetime

import torch
from torch import nn
from torch import optim
from torch.autograd import Variable
from torch.backends import cudnn
from torch.utils.data import DataLoader
from torchvision import transforms


from model.BDRAR_EX import BDRAR_6CH
from dataloaders.SBU import SBU_Merge
from dataloaders import joint_transforms
from utils.util import AvgMeter, check_mkdir

cudnn.benchmark = True

torch.cuda.set_device(0)

root = './'
ckpt_path = './ckpt'
exp_name = 'BDRAR_EX'

# batch size of 8 with resolution of 416*416 is exactly OK for the GTX 1080Ti GPU
args = {
    'iter_num': 5000,
    'train_batch_size': 8,
    'last_iter': 0,
    'lr': 5e-3,
    'lr_decay': 0.9,
    'weight_decay': 5e-4,
    'momentum': 0.9,
    'snapshot': '',
    'scale': 416
}

joint_transform = joint_transforms.Compose([
        joint_transforms.RandomHorizontallyFlip(),
        joint_transforms.Resize((416, 416))
    ])
src1_transform = transforms.Compose([
        transforms.ToTensor(),
        transforms.Normalize([0.485, 0.456, 0.406], [0.229, 0.224, 0.225])
    ])

src2_transform = transforms.ToTensor()
target_transform = transforms.ToTensor()
to_pil = transforms.ToPILImage()

db_train = SBU_Merge(root=root, joint_transform = joint_transform, src1_transform = src1_transform, src2_transform = src2_transform, target_transform = target_transform)
train_loader = DataLoader(db_train, batch_size=4, num_workers=8, shuffle=True)

bce_logit = nn.BCEWithLogitsLoss().cuda()
log_path = os.path.join(ckpt_path, exp_name, str(datetime.datetime.now()) + '.txt')


def main():
    net = BDRAR_6CH().cuda().train()

    optimizer = optim.SGD([
        {'params': [param for name, param in net.named_parameters() if name[-4:] == 'bias'],
         'lr': 2 * args['lr']},
        {'params': [param for name, param in net.named_parameters() if name[-4:] != 'bias'],
         'lr': args['lr'], 'weight_decay': args['weight_decay']}
    ], momentum=args['momentum'])

    if len(args['snapshot']) > 0:
        print('training resumes from \'%s\'' % args['snapshot'])
        net.load_state_dict(torch.load(os.path.join(ckpt_path, exp_name, args['snapshot'] + '.pth')))
        optimizer.load_state_dict(torch.load(os.path.join(ckpt_path, exp_name, args['snapshot'] + '_optim.pth')))
        optimizer.param_groups[0]['lr'] = 2 * args['lr']
        optimizer.param_groups[1]['lr'] = args['lr']

    check_mkdir(ckpt_path)
    check_mkdir(os.path.join(ckpt_path, exp_name))
    open(log_path, 'w').write(str(args) + '\n\n')
    train(net, optimizer)


def train(net, optimizer):
    curr_iter = args['last_iter']
    while True:
        train_loss_record, loss_fuse_record, loss1_h2l_record = AvgMeter(), AvgMeter(), AvgMeter()
        loss2_h2l_record, loss3_h2l_record, loss4_h2l_record = AvgMeter(), AvgMeter(), AvgMeter()
        loss1_l2h_record, loss2_l2h_record, loss3_l2h_record = AvgMeter(), AvgMeter(), AvgMeter()
        loss4_l2h_record = AvgMeter()

        for i, data in enumerate(train_loader):
            optimizer.param_groups[0]['lr'] = 2 * args['lr'] * (1 - float(curr_iter) / args['iter_num']
                                                                ) ** args['lr_decay']
            optimizer.param_groups[1]['lr'] = args['lr'] * (1 - float(curr_iter) / args['iter_num']
                                                            ) ** args['lr_decay']

            with torch.autograd.set_detect_anomaly(True):
                src1, src2, target = data['src1'], data['src2'], data['target']
                batch_size = src1.size(0)
                src1 = Variable(src1).cuda()
                src2 = Variable(src2).cuda()
                target = Variable(target).cuda()

            

                optimizer.zero_grad()

                fuse_predict, predict1_h2l, predict2_h2l, predict3_h2l, predict4_h2l, \
                predict1_l2h, predict2_l2h, predict3_l2h, predict4_l2h = net.forward(src1, src2)
                loss_fuse = bce_logit(fuse_predict, target)
                loss1_h2l = bce_logit(predict1_h2l, target)
                loss2_h2l = bce_logit(predict2_h2l, target)
                loss3_h2l = bce_logit(predict3_h2l, target)
                loss4_h2l = bce_logit(predict4_h2l, target)
                loss1_l2h = bce_logit(predict1_l2h, target)
                loss2_l2h = bce_logit(predict2_l2h, target)
                loss3_l2h = bce_logit(predict3_l2h, target)
                loss4_l2h = bce_logit(predict4_l2h, target)

                loss = loss_fuse + loss1_h2l + loss2_h2l + loss3_h2l + loss4_h2l + loss1_l2h + loss2_l2h + loss3_l2h + loss4_l2h
                loss.backward()
                optimizer.step()

                train_loss_record.update(loss.data, batch_size)
                loss_fuse_record.update(loss_fuse.data, batch_size)
                loss1_h2l_record.update(loss1_h2l.data, batch_size)
                loss2_h2l_record.update(loss2_h2l.data, batch_size)
                loss3_h2l_record.update(loss3_h2l.data, batch_size)
                loss4_h2l_record.update(loss4_h2l.data, batch_size)
                loss1_l2h_record.update(loss1_l2h.data, batch_size)
                loss2_l2h_record.update(loss2_l2h.data, batch_size)
                loss3_l2h_record.update(loss3_l2h.data, batch_size)
                loss4_l2h_record.update(loss4_l2h.data, batch_size)

            curr_iter += 1

            log = '[iter %d], [train loss %.5f], [loss_fuse %.5f], [loss1_h2l %.5f], [loss2_h2l %.5f], ' \
                  '[loss3_h2l %.5f], [loss4_h2l %.5f], [loss1_l2h %.5f], [loss2_l2h %.5f], [loss3_l2h %.5f], ' \
                  '[loss4_l2h %.5f], [lr %.13f]' % \
                  (curr_iter, train_loss_record.avg, loss_fuse_record.avg, loss1_h2l_record.avg, loss2_h2l_record.avg,
                   loss3_h2l_record.avg, loss4_h2l_record.avg, loss1_l2h_record.avg, loss2_l2h_record.avg,
                   loss3_l2h_record.avg, loss4_l2h_record.avg, optimizer.param_groups[1]['lr'])
            print(log)
            open(log_path, 'a').write(log + '\n')

            if curr_iter >= args['iter_num']:
                date = datetime.datetime.now().strftime('%Y-%m-%d %H:%M:%S')
                torch.save(net.state_dict(), os.path.join("RGB_LOG_GRAYSCALE.pth"))
                return


if __name__ == '__main__':
    main()

/usr/local/lib/python3.7/dist-packages/torch/utils/data/dataloader.py:477: UserWarning: This DataLoader will create 8 worker processes in total. Our suggested max number of worker in current system is 4, which is smaller than what this DataLoader is going to create. Please be aware that excessive worker creation might get DataLoader running slow or even freeze, lower the worker number to avoid potential slowness/freeze if necessary.
  cpuset_checked))
/usr/local/lib/python3.7/dist-packages/torch/nn/functional.py:3458: UserWarning: Default upsampling behavior when mode=bilinear is changed to align_corners=False since 0.4.0. Please specify align_corners=True if the old behavior is desired. See the documentation of nn.Upsample for details.
  "See the documentation of nn.Upsample for details.".format(mode)


스트리밍 출력 내용이 길어서 마지막 5000줄이 삭제되었습니다.
[iter 1], [train loss 5.98609], [loss_fuse 0.65739], [loss1_h2l 0.66723], [loss2_h2l 0.66481], [loss3_h2l 0.67004], [loss4_h2l 0.66712], [loss1_l2h 0.66923], [loss2_l2h 0.66249], [loss3_l2h 0.66317], [loss4_l2h 0.66462], [lr 0.0050000000000]
[iter 2], [train loss 5.88267], [loss_fuse 0.64389], [loss1_h2l 0.65263], [loss2_h2l 0.65451], [loss3_h2l 0.65830], [loss4_h2l 0.66021], [loss1_l2h 0.65667], [loss2_l2h 0.65157], [loss3_l2h 0.65231], [loss4_l2h 0.65257], [lr 0.0049990999910]
[iter 3], [train loss 5.76654], [loss_fuse 0.62946], [loss1_h2l 0.63967], [loss2_h2l 0.64514], [loss3_h2l 0.64556], [loss4_h2l 0.65122], [loss1_l2h 0.64102], [loss2_l2h 0.63762], [loss3_l2h 0.63929], [loss4_l2h 0.63755], [lr 0.0049981999640]
[iter 4], [train loss 5.60242], [loss_fuse 0.61264], [loss1_h2l 0.62346], [loss2_h2l 0.62699], [loss3_h2l 0.62633], [loss4_h2l 0.63170], [loss1_l2h 0.62120], [loss2_l2h 0.61898], [loss3_l2h 0.62103], [loss4_l2h 0.62008], [lr 0.00499729991

# 4. BDRAR_EDGE

In [ ]:
!unzip SBU_EDGE.zip

스트리밍 출력 내용이 길어서 마지막 5000줄이 삭제되었습니다.
  inflating: ShadowImages/lssd3853.jpg  
  inflating: ShadowImages/lssd3854.jpg  
  inflating: ShadowImages/lssd3855.jpg  
  inflating: ShadowImages/lssd3856.jpg  
  inflating: ShadowImages/lssd3857.jpg  
  inflating: ShadowImages/lssd3858.jpg  
  inflating: ShadowImages/lssd3859.jpg  
  inflating: ShadowImages/lssd386.jpg  
  inflating: ShadowImages/lssd3860.jpg  
  inflating: ShadowImages/lssd3861.jpg  
  inflating: ShadowImages/lssd3862.jpg  
  inflating: ShadowImages/lssd3863.jpg  
  inflating: ShadowImages/lssd3864.jpg  
  inflating: ShadowImages/lssd3865.jpg  
  inflating: ShadowImages/lssd3866.jpg  
  inflating: ShadowImages/lssd3867.jpg  
  inflating: ShadowImages/lssd3868.jpg  
  inflating: ShadowImages/lssd3869.jpg  
  inflating: ShadowImages/lssd387.jpg  
  inflating: ShadowImages/lssd3870.jpg  
  inflating: ShadowImages/lssd3871.jpg  
  inflating: ShadowImages/lssd3872.jpg  
  inflating: ShadowImages/lssd3873.jpg  
  inflating: ShadowImag

In [ ]:
import datetime
import os
import datetime

import torch
from torch import nn
from torch import optim
from torch.autograd import Variable
from torch.backends import cudnn
from torch.utils.data import DataLoader
from torchvision import transforms


from model.BDRAR_EX import BDRAR_6CH_EDGE
from dataloaders.SBU import SBU_EDGE 
from dataloaders import joint_transforms_edge as joint_transforms
from utils.util import AvgMeter, check_mkdir

cudnn.benchmark = True

torch.cuda.set_device(0)

root = './'
ckpt_path = './ckpt'
exp_name = 'BDRAR_EX'

# batch size of 8 with resolution of 416*416 is exactly OK for the GTX 1080Ti GPU
args = {
    'iter_num': 5000,
    'train_batch_size': 8,
    'last_iter': 0,
    'lr': 5e-3,
    'lr_decay': 0.9,
    'weight_decay': 5e-4,
    'edge': 10,
    'momentum': 0.9,
    'snapshot': '',
    'scale': 416
}

joint_transform = joint_transforms.Compose([
        joint_transforms.RandomHorizontallyFlip(),
        joint_transforms.Resize((416, 416))
    ])
src1_transform = transforms.Compose([
        transforms.ToTensor(),
        transforms.Normalize([0.485, 0.456, 0.406], [0.229, 0.224, 0.225])
    ])

src2_transform = transforms.ToTensor()
target_transform = transforms.ToTensor()
to_pil = transforms.ToPILImage()

db_train = SBU_EDGE(root=root, joint_transform = joint_transform, src1_transform = src1_transform, src2_transform = src2_transform, target_transform = target_transform, edge = True)
train_loader = DataLoader(db_train, batch_size=4, num_workers=8, shuffle=True)

bce_logit = nn.BCEWithLogitsLoss().cuda()
log_path = os.path.join(ckpt_path, exp_name, str(datetime.datetime.now()) + '.txt')


def main():
    net = BDRAR_6CH_EDGE().cuda().train()

    optimizer = optim.SGD([
        {'params': [param for name, param in net.named_parameters() if name[-4:] == 'bias'],
         'lr': 2 * args['lr']},
        {'params': [param for name, param in net.named_parameters() if name[-4:] != 'bias'],
         'lr': args['lr'], 'weight_decay': args['weight_decay']}
    ], momentum=args['momentum'])

    if len(args['snapshot']) > 0:
        print('training resumes from \'%s\'' % args['snapshot'])
        net.load_state_dict(torch.load(os.path.join(ckpt_path, exp_name, args['snapshot'] + '.pth')))
        optimizer.load_state_dict(torch.load(os.path.join(ckpt_path, exp_name, args['snapshot'] + '_optim.pth')))
        optimizer.param_groups[0]['lr'] = 2 * args['lr']
        optimizer.param_groups[1]['lr'] = args['lr']

    check_mkdir(ckpt_path)
    check_mkdir(os.path.join(ckpt_path, exp_name))
    open(log_path, 'w').write(str(args) + '\n\n')
    train(net, optimizer)


def train(net, optimizer):
    curr_iter = args['last_iter']
    while True:
        train_loss_record, loss_fuse_record, loss1_h2l_record = AvgMeter(), AvgMeter(), AvgMeter()
        loss2_h2l_record, loss3_h2l_record, loss4_h2l_record = AvgMeter(), AvgMeter(), AvgMeter()
        loss1_l2h_record, loss2_l2h_record, loss3_l2h_record = AvgMeter(), AvgMeter(), AvgMeter()
        loss4_l2h_record, loss_edge_record = AvgMeter(), AvgMeter()

        for i, data in enumerate(train_loader):
            optimizer.param_groups[0]['lr'] = 2 * args['lr'] * (1 - float(curr_iter) / args['iter_num']
                                                                ) ** args['lr_decay']
            optimizer.param_groups[1]['lr'] = args['lr'] * (1 - float(curr_iter) / args['iter_num']
                                                            ) ** args['lr_decay']

            with torch.autograd.set_detect_anomaly(True):
                src1, src2, target, edge = data['src1'], data['src2'], data['target'], data['edge']
                batch_size = src1.size(0)
                src1 = Variable(src1).cuda()
                src2 = Variable(src2).cuda()
                target = Variable(target).cuda()
                edge = Variable(edge).cuda()

            

                optimizer.zero_grad()

                fuse_predict, edge_predict, predict1_h2l, predict2_h2l, predict3_h2l, predict4_h2l, \
                predict1_l2h, predict2_l2h, predict3_l2h, predict4_l2h = net.forward(src1, src2)
                loss_fuse = bce_logit(fuse_predict, target)
                loss1_h2l = bce_logit(predict1_h2l, target)
                loss2_h2l = bce_logit(predict2_h2l, target)
                loss3_h2l = bce_logit(predict3_h2l, target)
                loss4_h2l = bce_logit(predict4_h2l, target)
                loss1_l2h = bce_logit(predict1_l2h, target)
                loss2_l2h = bce_logit(predict2_l2h, target)
                loss3_l2h = bce_logit(predict3_l2h, target)
                loss4_l2h = bce_logit(predict4_l2h, target)
                loss_edge = bce_logit(edge_predict, edge)

                loss_mask = loss_fuse + loss1_h2l + loss2_h2l + loss3_h2l + loss4_h2l + loss1_l2h + loss2_l2h + loss3_l2h + loss4_l2h
                loss = loss_mask + args['edge'] * loss_edge
                loss.backward()
                optimizer.step()

                train_loss_record.update(loss.data, batch_size)
                loss_fuse_record.update(loss_fuse.data, batch_size)
                loss1_h2l_record.update(loss1_h2l.data, batch_size)
                loss2_h2l_record.update(loss2_h2l.data, batch_size)
                loss3_h2l_record.update(loss3_h2l.data, batch_size)
                loss4_h2l_record.update(loss4_h2l.data, batch_size)
                loss1_l2h_record.update(loss1_l2h.data, batch_size)
                loss2_l2h_record.update(loss2_l2h.data, batch_size)
                loss3_l2h_record.update(loss3_l2h.data, batch_size)
                loss4_l2h_record.update(loss4_l2h.data, batch_size)
                loss_edge_record.update(loss_edge.data, batch_size)

            curr_iter += 1

            log = '[iter %d], [train loss %.5f], [loss_fuse %.5f], [loss_edge %.5f], [lr %.13f]' % \
                  (curr_iter, train_loss_record.avg, loss_fuse_record.avg, loss_edge_record.avg, optimizer.param_groups[1]['lr'])
            print(log)
            open(log_path, 'a').write(log + '\n')

            if curr_iter >= args['iter_num']:
                date = datetime.datetime.now().strftime('%Y-%m-%d %H:%M:%S')
                torch.save(net.state_dict(), os.path.join("6CH_EDGE.pth"))
                return


if __name__ == '__main__':
    main()

/usr/local/lib/python3.7/dist-packages/torch/utils/data/dataloader.py:477: UserWarning: This DataLoader will create 8 worker processes in total. Our suggested max number of worker in current system is 4, which is smaller than what this DataLoader is going to create. Please be aware that excessive worker creation might get DataLoader running slow or even freeze, lower the worker number to avoid potential slowness/freeze if necessary.
  cpuset_checked))
/usr/local/lib/python3.7/dist-packages/torch/nn/functional.py:3458: UserWarning: Default upsampling behavior when mode=bilinear is changed to align_corners=False since 0.4.0. Please specify align_corners=True if the old behavior is desired. See the documentation of nn.Upsample for details.
  "See the documentation of nn.Upsample for details.".format(mode)


스트리밍 출력 내용이 길어서 마지막 5000줄이 삭제되었습니다.
[iter 1], [train loss 13.30445], [loss_fuse 0.69568], [loss_edge 0.69902], [lr 0.0050000000000]
[iter 2], [train loss 13.03141], [loss_fuse 0.69024], [loss_edge 0.67946], [lr 0.0049990999910]
[iter 3], [train loss 12.62860], [loss_fuse 0.68030], [loss_edge 0.64874], [lr 0.0049981999640]
[iter 4], [train loss 12.08445], [loss_fuse 0.66297], [loss_edge 0.61192], [lr 0.0049972999190]
[iter 5], [train loss 11.50052], [loss_fuse 0.64264], [loss_edge 0.57259], [lr 0.0049963998560]
[iter 6], [train loss 10.96304], [loss_fuse 0.62551], [loss_edge 0.53458], [lr 0.0049954997749]
[iter 7], [train loss 10.38252], [loss_fuse 0.60387], [loss_edge 0.49708], [lr 0.0049945996759]
[iter 8], [train loss 9.82934], [loss_fuse 0.58139], [loss_edge 0.46250], [lr 0.0049936995588]
[iter 9], [train loss 9.34815], [loss_fuse 0.56294], [loss_edge 0.43093], [lr 0.0049927994237]
[iter 10], [train loss 8.85869], [loss_fuse 0.54117], [loss_edge 0.40163], [lr 0.0049918992705]
[iter 

# 7. EDGE + COUNT

In [ ]:
!unzip SBU_EDGE.zip

스트리밍 출력 내용이 길어서 마지막 5000줄이 삭제되었습니다.
  inflating: ShadowImages/lssd3853.jpg  
  inflating: ShadowImages/lssd3854.jpg  
  inflating: ShadowImages/lssd3855.jpg  
  inflating: ShadowImages/lssd3856.jpg  
  inflating: ShadowImages/lssd3857.jpg  
  inflating: ShadowImages/lssd3858.jpg  
  inflating: ShadowImages/lssd3859.jpg  
  inflating: ShadowImages/lssd386.jpg  
  inflating: ShadowImages/lssd3860.jpg  
  inflating: ShadowImages/lssd3861.jpg  
  inflating: ShadowImages/lssd3862.jpg  
  inflating: ShadowImages/lssd3863.jpg  
  inflating: ShadowImages/lssd3864.jpg  
  inflating: ShadowImages/lssd3865.jpg  
  inflating: ShadowImages/lssd3866.jpg  
  inflating: ShadowImages/lssd3867.jpg  
  inflating: ShadowImages/lssd3868.jpg  
  inflating: ShadowImages/lssd3869.jpg  
  inflating: ShadowImages/lssd387.jpg  
  inflating: ShadowImages/lssd3870.jpg  
  inflating: ShadowImages/lssd3871.jpg  
  inflating: ShadowImages/lssd3872.jpg  
  inflating: ShadowImages/lssd3873.jpg  
  inflating: ShadowImag

In [ ]:
import datetime
import os
import datetime

import torch
from torch import nn
from torch import optim
import torch.nn.functional as F
from torch.autograd import Variable
from torch.backends import cudnn
from torch.utils.data import DataLoader
from torchvision import transforms


from model.BDRAR_EX import BDRAR_6CH_EDGE_COUNT
from dataloaders.SBU import SBU_EDGE_COUNT 
from dataloaders import joint_transforms_edge as joint_transforms
from utils.util import AvgMeter, check_mkdir

cudnn.benchmark = True

torch.cuda.set_device(0)

root = './'
ckpt_path = './ckpt'
exp_name = 'BDRAR_EX'

# batch size of 8 with resolution of 416*416 is exactly OK for the GTX 1080Ti GPU
args = {
    'iter_num': 5000,
    'train_batch_size': 8,
    'last_iter': 0,
    'lr': 5e-3,
    'lr_decay': 0.9,
    'weight_decay': 5e-4,
    'edge': 10,
    'momentum': 0.9,
    'snapshot': '',
    'scale': 416
}

joint_transform = joint_transforms.Compose([
        joint_transforms.RandomHorizontallyFlip(),
        joint_transforms.Resize((416, 416))
    ])
src1_transform = transforms.Compose([
        transforms.ToTensor(),
        transforms.Normalize([0.485, 0.456, 0.406], [0.229, 0.224, 0.225])
    ])

src2_transform = transforms.ToTensor()
target_transform = transforms.ToTensor()
to_pil = transforms.ToPILImage()

db_train = SBU_EDGE_COUNT(root=root, joint_transform = joint_transform, src1_transform = src1_transform, src2_transform = src2_transform, target_transform = target_transform, edge = True)
train_loader = DataLoader(db_train, batch_size=4, num_workers=8, shuffle=True)

bce_logit = nn.BCEWithLogitsLoss().cuda()
log_path = os.path.join(ckpt_path, exp_name, str(datetime.datetime.now()) + '.txt')

def sigmoid_mse_loss(input_logits, target_logits):
    assert input_logits.size() == target_logits.size()
    input_sigmoid = F.sigmoid(input_logits)
    target_sigmoid = F.sigmoid(target_logits)
    return F.mse_loss(input_sigmoid, target_sigmoid, reduction='mean')


def main():
    net = BDRAR_6CH_EDGE_COUNT().cuda().train()

    optimizer = optim.SGD([
        {'params': [param for name, param in net.named_parameters() if name[-4:] == 'bias'],
         'lr': 2 * args['lr']},
        {'params': [param for name, param in net.named_parameters() if name[-4:] != 'bias'],
         'lr': args['lr'], 'weight_decay': args['weight_decay']}
    ], momentum=args['momentum'])

    if len(args['snapshot']) > 0:
        print('training resumes from \'%s\'' % args['snapshot'])
        net.load_state_dict(torch.load(os.path.join(ckpt_path, exp_name, args['snapshot'] + '.pth')))
        optimizer.load_state_dict(torch.load(os.path.join(ckpt_path, exp_name, args['snapshot'] + '_optim.pth')))
        optimizer.param_groups[0]['lr'] = 2 * args['lr']
        optimizer.param_groups[1]['lr'] = args['lr']

    check_mkdir(ckpt_path)
    check_mkdir(os.path.join(ckpt_path, exp_name))
    open(log_path, 'w').write(str(args) + '\n\n')
    train(net, optimizer)


def train(net, optimizer):
    curr_iter = args['last_iter']
    while True:
        train_loss_record, loss_fuse_record, loss_edge_record, loss_count_record = AvgMeter(), AvgMeter(), AvgMeter(), AvgMeter()

        for i, data in enumerate(train_loader):
            optimizer.param_groups[0]['lr'] = 2 * args['lr'] * (1 - float(curr_iter) / args['iter_num']
                                                                ) ** args['lr_decay']
            optimizer.param_groups[1]['lr'] = args['lr'] * (1 - float(curr_iter) / args['iter_num']
                                                            ) ** args['lr_decay']

            with torch.autograd.set_detect_anomaly(True):
                src1, src2, target, edge, count = data['src1'], data['src2'], data['target'], data['edge'], data['count']
                batch_size = src1.size(0)
                src1 = Variable(src1).cuda()
                src2 = Variable(src2).cuda()
                target = Variable(target).cuda()
                edge = Variable(edge).cuda()
                count = Variable(count).cuda()
            

                optimizer.zero_grad()

                fuse_predict, edge_predict, shadow_count, predict1_h2l, predict2_h2l, predict3_h2l, predict4_h2l, \
                predict1_l2h, predict2_l2h, predict3_l2h, predict4_l2h = net.forward(src1, src2)

                loss_fuse = bce_logit(fuse_predict, target)
                loss1_h2l = bce_logit(predict1_h2l, target)
                loss2_h2l = bce_logit(predict2_h2l, target)
                loss3_h2l = bce_logit(predict3_h2l, target)
                loss4_h2l = bce_logit(predict4_h2l, target)
                loss1_l2h = bce_logit(predict1_l2h, target)
                loss2_l2h = bce_logit(predict2_l2h, target)
                loss3_l2h = bce_logit(predict3_l2h, target)
                loss4_l2h = bce_logit(predict4_l2h, target)
                loss_edge = bce_logit(edge_predict, edge)
                loss_count = sigmoid_mse_loss(shadow_count, count)

                loss_mask = loss_fuse + loss1_h2l + loss2_h2l + loss3_h2l + loss4_h2l + loss1_l2h + loss2_l2h + loss3_l2h + loss4_l2h
                loss = loss_mask + args['edge'] * loss_edge + loss_count
                loss.backward()
                optimizer.step()

                train_loss_record.update(loss.data, batch_size)
                loss_fuse_record.update(loss_fuse.data, batch_size)
                loss_edge_record.update(loss_edge.data, batch_size)
                loss_count_record.update(loss_count.data, batch_size)

            curr_iter += 1

            log = '[iter %d], [train loss %.5f], [loss_fuse %.5f], [loss_edge %.5f], [loss_count %.5f], [lr %.13f]' % \
                  (curr_iter, train_loss_record.avg, loss_fuse_record.avg, loss_edge_record.avg, loss_count_record.avg, optimizer.param_groups[1]['lr'])
            print(log)
            open(log_path, 'a').write(log + '\n')

            if curr_iter >= args['iter_num']:
                date = datetime.datetime.now().strftime('%Y-%m-%d %H:%M:%S')
                torch.save(net.state_dict(), os.path.join("6CH_EDGE_COUNT.pth"))
                return


if __name__ == '__main__':
    main()

/usr/local/lib/python3.7/dist-packages/torch/utils/data/dataloader.py:477: UserWarning: This DataLoader will create 8 worker processes in total. Our suggested max number of worker in current system is 4, which is smaller than what this DataLoader is going to create. Please be aware that excessive worker creation might get DataLoader running slow or even freeze, lower the worker number to avoid potential slowness/freeze if necessary.
  cpuset_checked))
/usr/local/lib/python3.7/dist-packages/torch/nn/functional.py:3458: UserWarning: Default upsampling behavior when mode=bilinear is changed to align_corners=False since 0.4.0. Please specify align_corners=True if the old behavior is desired. See the documentation of nn.Upsample for details.
  "See the documentation of nn.Upsample for details.".format(mode)
/usr/local/lib/python3.7/dist-packages/torch/nn/functional.py:1709: UserWarning: nn.functional.sigmoid is deprecated. Use torch.sigmoid instead.
  warnings.warn("nn.functional.sigmoid is

스트리밍 출력 내용이 길어서 마지막 5000줄이 삭제되었습니다.
[iter 1], [train loss 14.90630], [loss_fuse 0.53188], [loss_edge 0.98788], [loss_count 0.15985], [lr 0.0050000000000]
[iter 2], [train loss 14.37096], [loss_fuse 0.50660], [loss_edge 0.95534], [loss_count 0.16290], [lr 0.0049990999910]
[iter 3], [train loss 13.67583], [loss_fuse 0.48478], [loss_edge 0.90644], [loss_count 0.16099], [lr 0.0049981999640]
[iter 4], [train loss 13.11747], [loss_fuse 0.49129], [loss_edge 0.84669], [loss_count 0.15588], [lr 0.0049972999190]
[iter 5], [train loss 12.51687], [loss_fuse 0.49556], [loss_edge 0.78276], [loss_count 0.15624], [lr 0.0049963998560]
[iter 6], [train loss 11.81215], [loss_fuse 0.48861], [loss_edge 0.71954], [loss_count 0.15252], [lr 0.0049954997749]
[iter 7], [train loss 10.97763], [loss_fuse 0.46287], [loss_edge 0.65946], [loss_count 0.14623], [lr 0.0049945996759]
[iter 8], [train loss 10.45649], [loss_fuse 0.46399], [loss_edge 0.60602], [loss_count 0.14368], [lr 0.0049936995588]
[iter 9], [train los

# 6. Else

In [ ]:
!cp ./6CH_EDGE_COUNT.pth "/content/gdrive/MyDrive/Weight/6CH_EDGE_COUNT.pth"

In [ ]:
!unzip test3.zip

Archive:  test3.zip
   creating: test3/
  inflating: test3/102.jpg           
  inflating: test3/201.jpg           
  inflating: test3/306.jpg           
  inflating: test3/417.jpg           
  inflating: test3/518.jpg           
  inflating: test3/90.jpg            


In [ ]:
import numpy as np
import os
import cv2

import torch
from PIL import Image
from torch.autograd import Variable
from torchvision import transforms

from dataloaders.SBU import make_merge_src
from model.BDRAR_EX import BDRAR_6CH_EDGE_COUNT
from dataloaders import joint_transforms_edge as joint_transforms
from utils.util import crf_refine
import matplotlib.pyplot as plt

torch.cuda.set_device(0)

ckpt_path = './ckpt'
exp_name = 'BDRAR_EX'
args = {
    'scale': 416
}

src1_transform = transforms.Compose([
        transforms.ToTensor(),
        transforms.Normalize([0.485, 0.456, 0.406], [0.229, 0.224, 0.225])
    ])

src2_transform = transforms.ToTensor()

target_transform = transforms.ToTensor()
to_pil = transforms.ToPILImage()

to_test = {'test3': "/content/BDRAR_EX/test3"}

loadpath = "/content/gdrive/MyDrive/Weight/6CH_EDGE_COUNT.pth"
if not os.path.exists("./Test"):
  os.mkdir("./Test")

def main():
    net = BDRAR_6CH_EDGE_COUNT().cuda()
    net.load_state_dict(torch.load(loadpath))
    net.eval()
    with torch.no_grad():
        for name, root in to_test.items():
            img_list = [img_name for img_name in os.listdir(root) if
                        img_name.endswith('.jpg')]
            for idx, img_name in enumerate(img_list):
                print('predicting for %s: %d / %d' % (name, idx + 1, len(img_list)))
                img = cv2.imread(os.path.join(root, img_name), cv2.IMREAD_COLOR)
                src1, src2 = make_merge_src(img)
                h, w, _ = np.array(src1).shape
                src1_var = src1_transform(src1)
                src1_var = (src1_var.unsqueeze(0)).cuda()
                src2_var = src2_transform(src2)
                src2_var = (src2_var.unsqueeze(0)).cuda()
                output = net(src1_var, src2_var)
                prediction = np.array(transforms.Resize((h,w))(to_pil(output.data.squeeze(0).cpu())))
                prediction = crf_refine(np.array(src1), prediction)
                Image.fromarray(prediction).save(
                    os.path.join("/content/BDRAR_EX/Test", "Test" + str(idx) + ".jpg"))


if __name__ == '__main__':
    main()

predicting for test3: 1 / 6


/usr/local/lib/python3.7/dist-packages/torch/nn/functional.py:3458: UserWarning: Default upsampling behavior when mode=bilinear is changed to align_corners=False since 0.4.0. Please specify align_corners=True if the old behavior is desired. See the documentation of nn.Upsample for details.
  "See the documentation of nn.Upsample for details.".format(mode)


predicting for test3: 2 / 6
predicting for test3: 3 / 6
predicting for test3: 4 / 6
predicting for test3: 5 / 6
predicting for test3: 6 / 6


In [ ]:
from google.colab import files

!zip 6CH_EDGE_COUNT.zip -r Test
files.download('./6CH_EDGE_COUNT.zip')

  adding: Test/ (stored 0%)
  adding: Test/Test4.jpg (deflated 3%)
  adding: Test/Test2.jpg (deflated 37%)
  adding: Test/Test0.jpg (deflated 37%)
  adding: Test/Test1.jpg (deflated 27%)
  adding: Test/Test5.jpg (deflated 26%)
  adding: Test/Test3.jpg (deflated 23%)


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>